In [4]:
import pandas as pd
import numpy as np
pd.set_option('display.max_columns', 25)

In [9]:
stats = pd.read_csv("stats.csv")

def get_min_age(player):
    return stats[stats['Player'] == player]['Age'].min()

stats['min_age'] = stats['Player'].apply(get_min_age)

stats.dropna(subset=['TOTAL_MP'], inplace = True) # removes 609 seasons where the player didn't play at all
stats = stats[stats['TOTAL_MP'] >= 100]

def get_total_seasons(player):
    return stats[stats['Player'] == player].shape[0]

stats['TOTAL_seasons'] = stats['Player'].apply(get_total_seasons)

def index_seasons(player, year):
    season_list = list(stats[stats['Player'] == player]['Year'])
    season_list.sort()
    return season_list.index(year)

stats['season_index'] = [index_seasons(player, year) for player, year in zip(stats['Player'], stats['Year'])]

In [10]:
# convert minutes played to % of available minutes played
# helps to account for seasons shortened by injury or lockout

stats['min_proportion'] = stats['TOTAL_MP'] / (stats['G'] * 40)

In [12]:
stats['3P%'].fillna(value = 0.15, inplace = True)

def fix_low_3pa(attempts, rate):
    if attempts <= 5:
        return 0.15
    
    elif attempts <= 15:
        if rate >= 0.25:
            return 0.25
        else:
            return np.max([0.12, rate])
        
    elif attempts <= 25:
        if rate >= 0.35:
            return 0.35
        else:
            return np.max([0.1, rate])
        
    else:
        return rate

stats['3P%'] = [fix_low_3pa(attempts, rate) for attempts,
                                  rate in zip(stats['TOTAL_3PA'], stats['3P%'])]

def fix_low_fta(attempts, rate):
    if attempts <= 10:
        return 0.75
    
    elif attempts <= 25:
        if rate >= 0.8:
            return 0.8
        else:
            return np.max([0.7, rate])
        
    elif attempts <= 50:
        if rate >= 0.85:
            return 0.85
        else:
            return np.max([0.60, rate])
        
    else:
        return rate

stats['FT%'] = [fix_low_fta(attempts, rate) for attempts,
                                  rate in zip(stats['TOTAL_FTA'], stats['FT%'])]
def fix_low_2pa(attempts, rate):
    if attempts <= 25:
        if rate >= 0.6:
            return 0.6
        else:
            return np.max([0.3, rate])
    else:
        return rate

stats['2P%'] = [fix_low_fta(attempts, rate) for attempts,
                                  rate in zip(stats['TOTAL_2PA'], stats['2P%'])]


In [13]:
# convert counting stats to per 36 minute
stats['two_point_attempts'] = stats['TOTAL_2PA'] / stats['TOTAL_MP'] * 36
stats['three_point_attempts'] = stats['TOTAL_3PA'] / stats['TOTAL_MP'] * 36
stats['free_throw_attempts'] = stats['TOTAL_FTA'] / stats['TOTAL_MP'] * 36
stats['defensive_rebounds'] = stats['TOTAL_DRB'] / stats['TOTAL_MP'] * 36
stats['offensive_rebounds'] = stats['TOTAL_ORB'] / stats['TOTAL_MP'] * 36
stats['assists'] = stats['TOTAL_AST'] / stats['TOTAL_MP'] * 36
stats['steals'] = stats['TOTAL_STL'] / stats['TOTAL_MP'] * 36
stats['blocks'] = stats['TOTAL_BLK'] / stats['TOTAL_MP'] * 36
stats['turnovers'] = stats['TOTAL_TOV'] / stats['TOTAL_MP'] * 36
stats['personal_fouls'] = stats['TOTAL_PF'] / stats['TOTAL_MP'] * 36

In [14]:
stats['3P%'] = stats['3P%'] * 1.8

In [15]:

def logit(p):
    if p > 0.95:
        p = 0.95
    if p < 0.05:
        p = 0.05
    return np.log(p/(1-p))

def sigmoid(x):
    return 1 / (1 + np.exp(-x))

In [16]:
stats['minutes_proportion'] = stats['min_proportion'].apply(logit)
stats['two_point_percentage'] = stats['2P%'].apply(logit)
stats['three_point_percentage'] = stats['3P%'].apply(logit)
stats['free_throw_percentage'] = stats['FT%'].apply(logit)

In [39]:
stats['Age2'] = stats['Age'] ** 2
stats['Age3'] = stats['Age'] ** 3

In [54]:
class MultiModelContainer:
    
    '''
    Object to function as a container for multiple linear models.
    Initialize with a dictionary where keys are targets and values are lists of features.
    '''
    
    def __init__(self, feature_dict, data):
        
        self.model_dict = {}
        self.feature_dict = feature_dict
        
        # initialize and fit models
        for target in feature_dict.keys():
            features = feature_dict[target]
            self.model_dict[target] = RandomForestRegressor(n_estimators = 75, max_depth = 6).fit(data[features], data[target])     

    def predict(self, targets, data, output_df = False, input_df = True, feature_map = None):
        
        switch = False
        
        for target in targets:
            # select features for target
            features = self.feature_dict[target]
            
            if input_df:
                # select model and input data for prediction
                preds = self.model_dict[target].predict(data[features])
            else:
                # if not using a df use feature map to select data from an array
                X = np.hstack(tuple([data[:,feature_map[feature]] for feature in features]))
                preds = self.model_dict[target].predict(X.reshape(-1,len(features)))
            
            if not switch:
                predictions = preds.reshape(-1,1)
                switch = True
                
            else:
                predictions = np.hstack((predictions, preds.reshape(-1,1)))
        
        if not output_df:
            return predictions
        
        else:
            return pd.DataFrame(predictions, columns = targets, index = data.index)

In [55]:
import pickle

with open('Models/FinalModelRF.pkl', 'rb') as file:
    FinalModel = pickle.load(file)
    
with open('Models/MinutesModelRF.pkl', 'rb') as file:
    MinutesModel = pickle.load(file)

# Future Predictions

In [56]:
features = ['Age', 'two_point_percentage', 'two_point_attempts', 'three_point_percentage',
       'three_point_attempts', 'free_throw_percentage', 'free_throw_attempts',
       'defensive_rebounds', 'offensive_rebounds', 'assists', 'steals',
       'blocks', 'turnovers', 'personal_fouls', 'Age2', 'Age3']

# map p1 features to column index of current version
p1_features = ['Age', 'two_point_percentage_p1', 'two_point_attempts_p1', 'three_point_percentage_p1',
       'three_point_attempts_p1', 'free_throw_percentage_p1', 'free_throw_attempts_p1',
       'defensive_rebounds_p1', 'offensive_rebounds_p1', 'assists_p1', 'steals_p1',
       'blocks_p1', 'turnovers_p1', 'personal_fouls_p1', 'Age2', 'Age3']

feature_map = {}

for feat in p1_features:
    feature_map[feat] = p1_features.index(feat)
    
targets = ['two_point_percentage', 'two_point_attempts', 'three_point_percentage',
       'three_point_attempts', 'free_throw_percentage', 'free_throw_attempts',
       'defensive_rebounds', 'offensive_rebounds', 'assists', 'steals',
       'blocks', 'turnovers', 'personal_fouls']

In [57]:
mask = np.array(stats['Year'] == 2021)
new_players = stats[mask]
new_players

Unnamed: 0                  Player Pos  Age   Tm   G  GS    MP   FG  \
630           630            Aaron Gordon  PF   25  DEN  50  50  27.7  4.6   
631           631           Austin Rivers  SG   28  DEN  36   7  23.5  2.9   
632           632                 Bol Bol  PF   21  DEN  32   2   5.0  0.8   
633           633        Facundo Campazzo  PG   29  DEN  65  19  21.9  1.8   
635           635          JaMychal Green  PF   30  DEN  58   5  19.3  3.0   
...           ...                     ...  ..  ...  ...  ..  ..   ...  ...   
13897       13897             Patty Mills  PG   32  SAS  68   1  24.8  3.7   
13898       13898  Quinndary Weatherspoon  SG   24  SAS  20   0   6.1  0.8   
13899       13899                Rudy Gay  PF   34  SAS  63   1  21.6  4.2   
13900       13900               Tre Jones  PG   21  SAS  37   1   7.3  1.0   
13901       13901              Trey Lyles  PF   25  SAS  23   9  15.6  1.9   

        FGA    FG%   3P  ...  offensive_rebounds   assists    steals  \
630    10.0  0.463  1.2  ...            2.002890  4.187861  0.858382   
631     6.8  0.424  1.5  ...            0.340828  3.450888  1.278107   
632     1.8  0.431  0.3  ...            0.000000  1.575000  0.675000   
633     4.8  0.381  1.2  ...            0.555789  5.861053  1.995789   
635     6.4  0.463  1.4  ...            2.732143  1.703571  0.835714   
...     ...    ...  ...  ...                 ...       ...       ...   
13897   9.0  0.412  2.4  ...            0.384570  3.461128  0.897329   
13898   1.8  0.457  0.1  ...            0.892562  2.380165  2.380165   
13899  10.0  0.420  1.7  ...            1.113402  2.332842  1.192931   
13900   2.1  0.474  0.1  ...            1.070632  5.219331  1.070632   
13901   3.9  0.478  0.6  ...            0.905028  1.407821  0.603352   

         blocks  turnovers  personal_fouls  minutes_proportion  \
630    0.884393   2.523121        2.315029            0.809486   
631    0.085207   1.533728        2.726627            0.350775   
632    2.250000   2.925000        3.150000           -1.945910   
633    0.353684   1.844211        3.334737            0.192904   
635    0.707143   1.703571        4.628571           -0.068993   
...         ...        ...             ...                 ...   
13897  0.064095   1.410089        1.730564            0.487364   
13898  0.595041   2.975207        5.355372           -1.724831   
13899  1.060383   1.723122        3.048601            0.155870   
13900  0.000000   1.739777        1.739777           -1.504490   
13901  0.100559   0.603352        1.307263           -0.450969   

       two_point_percentage  three_point_percentage  free_throw_percentage  \
630                0.132192                0.417981               0.623438   
631                0.040005                0.682068               0.895384   
632                0.405465                0.532217               0.847298   
633               -0.224944                0.547692               1.982994   
635                0.136210                0.935550               1.430633   
...                     ...                     ...                    ...   
13897              0.000000                0.730888               2.313635   
13898              0.405465               -0.844442               1.386294   
13899             -0.196631                0.780556               1.411485   
13900             -0.136210               -0.994623               1.386294   
13901              0.405465                0.532217               0.847298   

       Age2   Age3  
630     625  15625  
631     784  21952  
632     441   9261  
633     841  24389  
635     900  27000  
...     ...    ...  
13897  1024  32768  
13898   576  13824  
13899  1156  39304  
13900   441   9261  
13901   625  15625  

[468 rows x 119 columns]

In [58]:
print(list(new_players['Player']))

['Aaron Gordon', 'Austin Rivers', 'Bol Bol', 'Facundo Campazzo', 'JaMychal Green', 'JaVale McGee', 'Jamal Murray', 'Markus Howard', 'Michael Porter Jr.', 'Monte Morris', 'Nikola Jokić', 'PJ Dozier', 'Paul Millsap', 'Shaquille Harrison', 'Vlatko Čančar', 'Will Barton', 'Zeke Nnaji', 'Aaron Holiday', 'Caris LeVert', 'Domantas Sabonis', 'Doug McDermott', 'Edmond Sumner', 'Goga Bitadze', 'JaKarr Sampson', 'Jeremy Lamb', 'Justin Holiday', 'Kelan Martin', 'Malcolm Brogdon', 'Myles Turner', 'Oshae Brissett', 'T.J. McConnell', 'T.J. Warren', 'Aaron Nesmith', 'Carsen Edwards', 'Evan Fournier', 'Grant Williams', 'Jabari Parker', 'Jaylen Brown', 'Jayson Tatum', 'Kemba Walker', 'Luke Kornet', 'Marcus Smart', 'Payton Pritchard', 'Robert Williams', 'Romeo Langford', 'Semi Ojeleye', 'Tacko Fall', 'Tremont Waters', 'Tristan Thompson', 'Abdel Nader', 'Cameron Johnson', 'Cameron Payne', 'Chris Paul', 'Dario Šarić', 'Deandre Ayton', 'Devin Booker', "E'Twaun Moore", 'Frank Kaminsky', 'Jae Crowder', 'Jalen

In [59]:
new_players.shape

(468, 119)

In [115]:
def predict_career(player_id, n_years, start_year, stats_model, minutes_model):
    
    # get the players actual data and create seed for predictions
    mask = np.array(stats['Player'] == player_id) & np.array(stats['Year'] == start_year)
    seed = np.array(stats[mask][features]).reshape(1,-1)
    mseed = np.array(stats[mask]['minutes_proportion']).reshape(-1,1)
    
    # iterate through total seasons and generate prediction based on each past prediction
    for i in range(0, n_years):
        
        # get inputs for prediction, previous season stats and CURRENT age
        pred_inputs = seed[-1,1:-2].reshape(1,-1)
        current_age = np.array(seed[i,0] + 1).reshape(1,-1)
        pred_inputs = np.hstack((current_age, pred_inputs, current_age**2, current_age**3))
        preds = stats_model.predict(targets, pred_inputs, input_df = False, feature_map = feature_map)
        
        # append age features to prediction
        preds = np.hstack((current_age, preds, current_age**2, current_age**3))
        
        # append predictions to seed
        seed = np.vstack((seed, preds))
    
    # predict minutes in each season
    for i in range(0, n_years):
        pred_inputs = np.hstack((seed[i+1,:], mseed[-1,:])).reshape(1,-1)
        minutes = minutes_model.predict(pred_inputs)
        mseed = np.vstack((mseed, minutes.reshape(-1,1)))
        
    seed = np.hstack((mseed, seed))
    
    # Convert logits back to percentages
    seed[:,0] = sigmoid(seed[:,0])
    
    for i, feat in enumerate(features):
        if feat[-10:] == 'percentage':
            seed[:,i + 1] = sigmoid(seed[:,i + 1])
    
    # Remove age2 and age3 features
    seed = seed[:,:-2]
    
    # Output Formatting
    cols = ['minutes_proportion'] + features[:-2]
    seed = pd.DataFrame(np.round(seed, 3), columns = cols)
    seed['Player'] = player_id
    #seed['name'] = seasons[mask]['name'][0]
    seed['Year'] = [start_year + i for i in range(n_years + 1)]
    seed['index_col'] = [str(player_id) + str(year) for player_id, year in zip(seed['Player'], seed['Year'])]
    seed.set_index('index_col', inplace = True)
    
    # Adjust 3pt percentage by dividing by 1.8
    seed['three_point_percentage'] = seed['three_point_percentage'] / 1.8
    
    #order columns for output
    final_cols = ['Player', 'Year'] + cols
    
    return seed[final_cols]

In [116]:
from IPython.display import HTML
HTML('''<script>
code_show_err=false; 
function code_toggle_err() {
 if (code_show_err){
 $('div.output_stderr').hide();
 } else {
 $('div.output_stderr').show();
 }
 code_show_err = !code_show_err
} 
$( document ).ready(code_toggle_err);
</script>
To toggle on/off output_stderr, click <a href="javascript:code_toggle_err()">here</a>.''')

In [150]:
career_preds = {}

for player_id in list(new_players['Player']):
    career_preds[player_id] = predict_career(player_id, 5, 2021, FinalModel, MinutesModel)

C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\ba

C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\ba

C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\ba

C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\ba

C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\ba

...

C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\ba

C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\ba

C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\ba

C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\ba

C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
C:\Users\Cillian\anaconda3\lib\site-packages\sklearn\ba

In [151]:
career_preds

{'Aaron Gordon':                         Player  Year  minutes_proportion   Age  \
 index_col                                                        
 Aaron Gordon2021  Aaron Gordon  2021               0.692  25.0   
 Aaron Gordon2022  Aaron Gordon  2022               0.715  26.0   
 Aaron Gordon2023  Aaron Gordon  2023               0.744  27.0   
 Aaron Gordon2024  Aaron Gordon  2024               0.742  28.0   
 Aaron Gordon2025  Aaron Gordon  2025               0.735  29.0   
 Aaron Gordon2026  Aaron Gordon  2026               0.722  30.0   
 
                   two_point_percentage  two_point_attempts  \
 index_col                                                    
 Aaron Gordon2021                 0.533               8.402   
 Aaron Gordon2022                 0.516               8.264   
 Aaron Gordon2023                 0.507               8.155   
 Aaron Gordon2024                 0.502               7.613   
 Aaron Gordon2025                 0.501               7.522   
 Aaro

# Per Game Averages

In [152]:
from copy import deepcopy

In [153]:
def per_game_averages(player_df):
    pg = deepcopy(player_df)
    
    pg['minutes_per_game'] = pg['minutes_proportion'] * 40
    pg.drop(columns = 'minutes_proportion', inplace = True)
    
    pg['two_pointers'] = pg['two_point_attempts'] * pg['two_point_percentage'] * pg['minutes_per_game'] / 36
    
    pg['three_pointers'] = pg['three_point_attempts'] * pg['three_point_percentage'] * pg['minutes_per_game'] / 36
    
    pg['free_throws'] = pg['free_throw_attempts'] * pg['free_throw_percentage'] * pg['minutes_per_game'] / 36

    pg['defensive_rebounds'] = pg['defensive_rebounds'] * pg['minutes_per_game'] / 36
    
    pg['offensive_rebounds'] = pg['offensive_rebounds'] * pg['minutes_per_game'] / 36
    
    pg['total_rebounds'] = pg['defensive_rebounds'] + pg['offensive_rebounds']
    
    pg['assists'] = pg['assists'] * pg['minutes_per_game'] / 36
    
    pg['steals'] = pg['steals'] * pg['minutes_per_game'] / 36
    
    pg['blocks'] = pg['blocks'] * pg['minutes_per_game'] / 36
    
    pg['turnovers'] = pg['turnovers'] * pg['minutes_per_game'] / 36
    
    pg['personal_fouls'] = pg['personal_fouls'] * pg['minutes_per_game'] / 36
    
    pg['points'] = 2 * pg['two_pointers'] + 3 * pg['three_pointers'] + 1 * pg['free_throws']
    
    pg['field_goals'] = pg['two_pointers'] + pg['three_pointers']
    
    pg['field_goal_percentage'] = pg['field_goals'] / ((pg['two_point_attempts'] + pg['three_point_attempts']) * pg['minutes_per_game'] / 36)
    
    final_columns = ['Player', 'Year', 'Age', 'minutes_per_game', 'field_goals', 'field_goal_percentage',
                     'three_pointers', 'three_point_percentage', 'two_pointers', 'two_point_percentage',  'free_throws',
                     'free_throw_percentage', 'total_rebounds', 'offensive_rebounds', 'defensive_rebounds',
                     'assists', 'steals', 'blocks', 'turnovers', 'personal_fouls', 'points']
    
    pg = pg.round(2)
    
    return pg[final_columns]

In [154]:
per_game_preds = {}

for player_id in career_preds.keys():

    per_game_preds[player_id] = per_game_averages(career_preds[player_id])

# Leaders

In [155]:
# Combine all the dataframes

switch = 0

for player_id in per_game_preds.keys():
    
    if not switch:
        per_game_df = per_game_preds[player_id]
        switch = 1
    
    else:
        per_game_df = pd.concat([per_game_df, per_game_preds[player_id]], axis = 0)

In [156]:
def stat_leaders(year, stat, N):
    
    stat_df = per_game_df[per_game_df['Year'] == year][['Player', stat]]
    return stat_df.sort_values(stat, ascending = False).head(N)

In [157]:
per_game_df[per_game_df['Year'] == 2022][['Player','Age','points']]

Player   Age  points
index_col                                                       
Aaron Gordon2022                      Aaron Gordon  26.0   12.65
Austin Rivers2022                    Austin Rivers  29.0    7.70
Bol Bol2022                                Bol Bol  22.0    8.58
Facundo Campazzo2022              Facundo Campazzo  30.0    6.52
JaMychal Green2022                  JaMychal Green  31.0    7.83
...                                            ...   ...     ...
Patty Mills2022                        Patty Mills  33.0   11.06
Quinndary Weatherspoon2022  Quinndary Weatherspoon  25.0    6.69
Rudy Gay2022                              Rudy Gay  35.0   11.96
Tre Jones2022                            Tre Jones  22.0    6.61
Trey Lyles2022                          Trey Lyles  26.0    6.67

[468 rows x 3 columns]

In [175]:
stat_leaders(2022, 'points', 10)

Player  points
index_col                                               
Bradley Beal2022                    Bradley Beal   28.21
Damian Lillard2022                Damian Lillard   26.74
Luka Dončić2022                      Luka Dončić   26.62
Joel Embiid2022                      Joel Embiid   26.35
Donovan Mitchell2022            Donovan Mitchell   25.44
Jayson Tatum2022                    Jayson Tatum   25.19
Stephen Curry2022                  Stephen Curry   24.90
Giannis Antetokounmpo2022  Giannis Antetokounmpo   24.50
Kyrie Irving2022                    Kyrie Irving   24.40
De'Aaron Fox2022                    De'Aaron Fox   24.23

In [159]:
stat_leaders(2022, 'total_rebounds', 10)

Player  total_rebounds
index_col                                                       
Clint Capela2022                    Clint Capela           13.31
Jonas Valančiūnas2022          Jonas Valančiūnas           12.32
Rudy Gobert2022                      Rudy Gobert           12.25
Joel Embiid2022                      Joel Embiid           10.95
Domantas Sabonis2022            Domantas Sabonis           10.95
Russell Westbrook2022          Russell Westbrook           10.69
Nikola Jokić2022                    Nikola Jokić           10.42
Enes Freedom2022                    Enes Freedom           10.31
Andre Drummond2022                Andre Drummond           10.27
Giannis Antetokounmpo2022  Giannis Antetokounmpo           10.17

In [160]:
stat_leaders(2022, 'assists', 10)

Player  assists
index_col                                        
Russell Westbrook2022  Russell Westbrook     9.52
James Harden2022            James Harden     9.34
Trae Young2022                Trae Young     9.03
Chris Paul2022                Chris Paul     8.33
Luka Dončić2022              Luka Dončić     8.32
Nikola Jokić2022            Nikola Jokić     7.88
LeBron James2022            LeBron James     7.45
Draymond Green2022        Draymond Green     7.22
Ben Simmons2022              Ben Simmons     7.20
Damian Lillard2022        Damian Lillard     7.03

In [161]:
stat_leaders(2022, 'steals', 10)

Player  steals
index_col                                     
Jimmy Butler2022          Jimmy Butler    1.73
Matisse Thybulle2022  Matisse Thybulle    1.67
T.J. McConnell2022      T.J. McConnell    1.66
Ben Simmons2022            Ben Simmons    1.54
LaMelo Ball2022            LaMelo Ball    1.50
Fred VanVleet2022        Fred VanVleet    1.44
De'Aaron Fox2022          De'Aaron Fox    1.44
Jrue Holiday2022          Jrue Holiday    1.44
Larry Nance Jr.2022    Larry Nance Jr.    1.43
Kawhi Leonard2022        Kawhi Leonard    1.40

In [162]:
stat_leaders(2022, 'blocks', 10)

Player  blocks
index_col                                       
Myles Turner2022            Myles Turner    2.65
Rudy Gobert2022              Rudy Gobert    2.13
Clint Capela2022            Clint Capela    1.90
Nerlens Noel2022            Nerlens Noel    1.64
Jakob Poeltl2022            Jakob Poeltl    1.60
Anthony Davis2022          Anthony Davis    1.48
Robert Williams2022      Robert Williams    1.43
Jarrett Allen2022          Jarrett Allen    1.41
Mitchell Robinson2022  Mitchell Robinson    1.39
Goga Bitadze2022            Goga Bitadze    1.37

In [163]:
stat_leaders(2022, 'three_pointers', 10)

Player  three_pointers
index_col                                             
Damian Lillard2022      Damian Lillard            3.95
Stephen Curry2022        Stephen Curry            3.75
Donovan Mitchell2022  Donovan Mitchell            3.34
Fred VanVleet2022        Fred VanVleet            3.31
D'Angelo Russell2022  D'Angelo Russell            3.15
CJ McCollum2022            CJ McCollum            3.07
Malik Beasley2022        Malik Beasley            3.06
Buddy Hield2022            Buddy Hield            3.01
Luka Dončić2022            Luka Dončić            2.98
Kemba Walker2022          Kemba Walker            2.93

In [164]:
stat_leaders(2022, 'free_throws', 10)

Player  free_throws
index_col                                                    
Joel Embiid2022                      Joel Embiid         7.16
Trae Young2022                        Trae Young         6.83
Bradley Beal2022                    Bradley Beal         6.14
Damian Lillard2022                Damian Lillard         6.01
Jimmy Butler2022                    Jimmy Butler         5.84
Giannis Antetokounmpo2022  Giannis Antetokounmpo         5.78
James Harden2022                    James Harden         5.71
Zion Williamson2022              Zion Williamson         5.57
DeMar DeRozan2022                  DeMar DeRozan         5.54
Kevin Durant2022                    Kevin Durant         5.34

In [165]:
stat_leaders(2022, 'minutes_per_game', 10)

Player  minutes_per_game
index_col                                                 
Julius Randle2022          Julius Randle             36.40
Bradley Beal2022            Bradley Beal             35.80
James Harden2022            James Harden             35.76
Jayson Tatum2022            Jayson Tatum             35.72
Damian Lillard2022        Damian Lillard             35.64
Zach LaVine2022              Zach LaVine             35.60
Collin Sexton2022          Collin Sexton             35.56
Russell Westbrook2022  Russell Westbrook             35.52
De'Aaron Fox2022            De'Aaron Fox             35.48
Pascal Siakam2022          Pascal Siakam             35.28

In [166]:
stat_leaders(2022, 'three_point_percentage', 10)

Player  three_point_percentage
index_col                                                       
Dakota Mathias2022        Dakota Mathias                    0.40
Seth Curry2022                Seth Curry                    0.40
Cameron Payne2022          Cameron Payne                    0.40
Kevin Durant2022            Kevin Durant                    0.40
Jeremy Lamb2022              Jeremy Lamb                    0.39
Kyrie Irving2022            Kyrie Irving                    0.39
Tyrese Haliburton2022  Tyrese Haliburton                    0.39
Killian Tillie2022        Killian Tillie                    0.39
Reggie Bullock2022        Reggie Bullock                    0.39
Stephen Curry2022          Stephen Curry                    0.39

In [167]:
per_game_df[np.array(per_game_df['Player'] == 'Stephen Curry') & np.array(per_game_df['Year'] == 2022)]

Player  Year   Age  minutes_per_game  field_goals  \
index_col                                                                     
Stephen Curry2022  Stephen Curry  2022  33.0             33.28         8.17   

                   field_goal_percentage  three_pointers  \
index_col                                                  
Stephen Curry2022                   0.46            3.75   

                   three_point_percentage  two_pointers  two_point_percentage  \
index_col                                                                       
Stephen Curry2022                    0.39          4.41                  0.53   

                   free_throws  free_throw_percentage  total_rebounds  \
index_col                                                               
Stephen Curry2022         4.82                   0.89            5.09   

                   offensive_rebounds  defensive_rebounds  assists  steals  \
index_col                                                                    
Stephen Curry2022                0.52                4.57     5.39    1.14   

                   blocks  turnovers  personal_fouls  points  
index_col                                                     
Stephen Curry2022    0.16       3.06            2.02    24.9

In [168]:
per_game_df[per_game_df['Player'] == 'LeBron James']

Player  Year   Age  minutes_per_game  field_goals  \
index_col                                                                   
LeBron James2021  LeBron James  2021  36.0             33.44         9.38   
LeBron James2022  LeBron James  2022  37.0             32.12         7.86   
LeBron James2023  LeBron James  2023  38.0             31.72         7.44   
LeBron James2024  LeBron James  2024  39.0             31.64         6.98   
LeBron James2025  LeBron James  2025  40.0             31.76         6.63   
LeBron James2026  LeBron James  2026  41.0             31.68         6.29   

                  field_goal_percentage  three_pointers  \
index_col                                                 
LeBron James2021                   0.51            2.31   
LeBron James2022                   0.47            1.85   
LeBron James2023                   0.47            1.82   
LeBron James2024                   0.45            1.86   
LeBron James2025                   0.44            1.88   
LeBron James2026                   0.44            1.87   

                  three_point_percentage  two_pointers  two_point_percentage  \
index_col                                                                      
LeBron James2021                    0.36          7.07                  0.59   
LeBron James2022                    0.34          6.02                  0.54   
LeBron James2023                    0.34          5.62                  0.53   
LeBron James2024                    0.34          5.12                  0.51   
LeBron James2025                    0.34          4.76                  0.50   
LeBron James2026                    0.34          4.42                  0.50   

                  free_throws  free_throw_percentage  total_rebounds  \
index_col                                                              
LeBron James2021         3.96                   0.70            7.69   
LeBron James2022         3.66                   0.75            7.11   
LeBron James2023         3.19                   0.78            6.76   
LeBron James2024         2.94                   0.78            6.38   
LeBron James2025         2.92                   0.78            6.08   
LeBron James2026         2.63                   0.78            6.12   

                  offensive_rebounds  defensive_rebounds  assists  steals  \
index_col                                                                   
LeBron James2021                0.64                7.05     7.78    1.07   
LeBron James2022                0.68                6.44     7.45    1.07   
LeBron James2023                0.70                6.06     6.97    1.07   
LeBron James2024                0.71                5.66     8.10    1.06   
LeBron James2025                0.72                5.35     7.73    1.07   
LeBron James2026                0.72                5.39     7.66    1.07   

                  blocks  turnovers  personal_fouls  points  
index_col                                                    
LeBron James2021    0.56       3.74            1.56   25.04  
LeBron James2022    0.49       3.22            1.79   21.23  
LeBron James2023    0.46       2.92            1.94   19.88  
LeBron James2024    0.44       2.73            2.28   18.76  
LeBron James2025    0.43       2.47            2.40   18.06  
LeBron James2026    0.43       2.30            2.44   17.09

In [169]:
per_game_df[per_game_df['Player'] == 'Giannis Antetokounmpo']

Player  Year   Age  \
index_col                                                      
Giannis Antetokounmpo2021  Giannis Antetokounmpo  2021  26.0   
Giannis Antetokounmpo2022  Giannis Antetokounmpo  2022  27.0   
Giannis Antetokounmpo2023  Giannis Antetokounmpo  2023  28.0   
Giannis Antetokounmpo2024  Giannis Antetokounmpo  2024  29.0   
Giannis Antetokounmpo2025  Giannis Antetokounmpo  2025  30.0   
Giannis Antetokounmpo2026  Giannis Antetokounmpo  2026  31.0   

                           minutes_per_game  field_goals  \
index_col                                                  
Giannis Antetokounmpo2021             33.00        10.26   
Giannis Antetokounmpo2022             33.20         8.74   
Giannis Antetokounmpo2023             32.92         8.17   
Giannis Antetokounmpo2024             32.76         7.95   
Giannis Antetokounmpo2025             32.48         7.59   
Giannis Antetokounmpo2026             31.96         7.28   

                           field_goal_percentage  three_pointers  \
index_col                                                          
Giannis Antetokounmpo2021                   0.57            1.10   
Giannis Antetokounmpo2022                   0.52            1.23   
Giannis Antetokounmpo2023                   0.50            1.30   
Giannis Antetokounmpo2024                   0.49            1.40   
Giannis Antetokounmpo2025                   0.49            1.45   
Giannis Antetokounmpo2026                   0.49            1.43   

                           three_point_percentage  two_pointers  \
index_col                                                         
Giannis Antetokounmpo2021                    0.30          9.16   
Giannis Antetokounmpo2022                    0.33          7.52   
Giannis Antetokounmpo2023                    0.34          6.88   
Giannis Antetokounmpo2024                    0.34          6.55   
Giannis Antetokounmpo2025                    0.34          6.14   
Giannis Antetokounmpo2026                    0.34          5.86   

                           two_point_percentage  free_throws  \
index_col                                                      
Giannis Antetokounmpo2021                  0.64         6.52   
Giannis Antetokounmpo2022                  0.57         5.78   
Giannis Antetokounmpo2023                  0.55         5.46   
Giannis Antetokounmpo2024                  0.54         5.01   
Giannis Antetokounmpo2025                  0.54         4.71   
Giannis Antetokounmpo2026                  0.55         4.36   

                           free_throw_percentage  total_rebounds  \
index_col                                                          
Giannis Antetokounmpo2021                   0.68           11.00   
Giannis Antetokounmpo2022                   0.72           10.17   
Giannis Antetokounmpo2023                   0.75           10.00   
Giannis Antetokounmpo2024                   0.75            9.46   
Giannis Antetokounmpo2025                   0.75            9.18   
Giannis Antetokounmpo2026                   0.75            8.86   

                           offensive_rebounds  defensive_rebounds  assists  \
index_col                                                                    
Giannis Antetokounmpo2021                1.59                9.41     5.85   
Giannis Antetokounmpo2022                1.49                8.68     5.50   
Giannis Antetokounmpo2023                1.87                8.14     5.24   
Giannis Antetokounmpo2024                1.94                7.52     5.01   
Giannis Antetokounmpo2025                1.93                7.25     4.78   
Giannis Antetokounmpo2026                1.90                6.96     4.58   

                           steals  blocks  turnovers  personal_fouls  points  
index_col                                                                     
Giannis Antetokounmpo2021    1.18    1.20       3.39            2.75   28.14  
Giannis Antetokounmpo2022    1.15    1.14     

In [170]:
per_game_df[per_game_df['Player'] == 'Luka Dončić']

Player  Year   Age  minutes_per_game  field_goals  \
index_col                                                                 
Luka Dončić2021  Luka Dončić  2021  21.0             34.28         9.81   
Luka Dončić2022  Luka Dončić  2022  22.0             34.68         9.27   
Luka Dončić2023  Luka Dončić  2023  23.0             34.84         9.31   
Luka Dončić2024  Luka Dončić  2024  24.0             35.60         9.30   
Luka Dončić2025  Luka Dončić  2025  25.0             35.68         9.01   
Luka Dončić2026  Luka Dončić  2026  26.0             35.72         8.74   

                 field_goal_percentage  three_pointers  \
index_col                                                
Luka Dončić2021                   0.48            2.91   
Luka Dončić2022                   0.45            2.98   
Luka Dončić2023                   0.43            3.34   
Luka Dončić2024                   0.43            3.56   
Luka Dončić2025                   0.42            3.56   
Luka Dončić2026                   0.42            3.56   

                 three_point_percentage  two_pointers  two_point_percentage  \
index_col                                                                     
Luka Dončić2021                    0.35          6.90                  0.57   
Luka Dončić2022                    0.34          6.29                  0.53   
Luka Dončić2023                    0.34          5.97                  0.50   
Luka Dončić2024                    0.34          5.75                  0.50   
Luka Dončić2025                    0.34          5.45                  0.50   
Luka Dončić2026                    0.34          5.19                  0.50   

                 free_throws  free_throw_percentage  total_rebounds  \
index_col                                                             
Luka Dončić2021         5.21                   0.73            7.99   
Luka Dončić2022         5.11                   0.76            7.68   
Luka Dončić2023         5.11                   0.78            7.24   
Luka Dončić2024         4.96                   0.79            6.90   
Luka Dončić2025         4.60                   0.79            6.84   
Luka Dončić2026         4.28                   0.79            6.84   

                 offensive_rebounds  defensive_rebounds  assists  steals  \
index_col                                                                  
Luka Dončić2021                0.82                7.17     8.59    0.97   
Luka Dončić2022                0.90                6.77     8.32    1.32   
Luka Dončić2023                0.93                6.32     8.15    1.25   
Luka Dončić2024                0.94                5.95     8.46    1.24   
Luka Dončić2025                0.92                5.92     8.30    1.23   
Luka Dončić2026                0.91                5.93     8.31    1.23   

                 blocks  turnovers  personal_fouls  points  
index_col                                                   
Luka Dončić2021    0.55       4.26            2.30   27.73  
Luka Dončić2022    0.53       3.82            2.50   26.62  
Luka Dončić2023    0.51       3.46            2.61   27.08  
Luka Dončić2024    0.52       3.32            2.72   27.12  
Luka Dončić2025    0.49       3.20            2.74   26.18  
Luka Dončić2026    0.49       3.11            2.74   25.33

In [171]:
per_game_df[per_game_df['Player'] == 'Chris Paul']

Player  Year   Age  minutes_per_game  field_goals  \
index_col                                                               
Chris Paul2021  Chris Paul  2021  35.0             31.40         6.27   
Chris Paul2022  Chris Paul  2022  36.0             30.60         5.67   
Chris Paul2023  Chris Paul  2023  37.0             29.92         5.14   
Chris Paul2024  Chris Paul  2024  38.0             29.00         4.74   
Chris Paul2025  Chris Paul  2025  39.0             28.80         6.21   
Chris Paul2026  Chris Paul  2026  40.0             28.80         5.82   

                field_goal_percentage  three_pointers  three_point_percentage  \
index_col                                                                       
Chris Paul2021                   0.50            1.46                    0.39   
Chris Paul2022                   0.48            1.47                    0.39   
Chris Paul2023                   0.45            1.46                    0.37   
Chris Paul2024                   0.44            1.40                    0.36   
Chris Paul2025                   0.45            1.44                    0.36   
Chris Paul2026                   0.45            1.48                    0.35   

                two_pointers  two_point_percentage  free_throws  \
index_col                                                         
Chris Paul2021          4.81                  0.54         2.41   
Chris Paul2022          4.20                  0.52         2.14   
Chris Paul2023          3.68                  0.50         2.01   
Chris Paul2024          3.34                  0.49         1.85   
Chris Paul2025          4.76                  0.49         1.77   
Chris Paul2026          4.34                  0.49         1.79   

                free_throw_percentage  total_rebounds  offensive_rebounds  \
index_col                                                                   
Chris Paul2021                   0.93            4.45                0.36   
Chris Paul2022                   0.88            4.36                0.46   
Chris Paul2023                   0.88            4.05                0.46   
Chris Paul2024                   0.86            3.81                0.44   
Chris Paul2025                   0.84            3.78                0.44   
Chris Paul2026                   0.82            3.78                0.44   

                defensive_rebounds  assists  steals  blocks  turnovers  \
index_col                                                                
Chris Paul2021                4.10     8.88    1.41    0.27       2.23   
Chris Paul2022                3.90     8.33    1.31    0.28       2.12   
Chris Paul2023                3.59     7.53    1.20    0.28       2.04   
Chris Paul2024                3.37     6.82    1.14    0.27       1.98   
Chris Paul2025                3.34     6.52    1.10    0.27       1.96   
Chris Paul2026                3.34     6.84    1.08    0.27       1.96   

                personal_fouls  points  
index_col                               
Chris Paul2021            2.37   16.41  
Chris Paul2022            2.35   14.95  
Chris Paul2023            2.31   13.74  
Chris Paul2024            2.24   12.74  
Chris Paul2025            2.23   15.62  
Chris Paul2026            2.23   14.90